In [1]:
import os
import re
import pandas as pd
import numpy as np
from dotenv import load_dotenv
from pathlib import Path
import panel as pn
import plotly.express as px
import plotly.graph_objects as go
pn.extension("plotly") 
from panel.interact import interact
import hvplot.pandas
import pandas_datareader as pdr
import seaborn as sns

%matplotlib inline

   # Data on Stock Financial Analysis

In [2]:
# Read the Mapbox API key
load_dotenv()
mapbox_token = os.getenv("MAPBOX_API_KEY")
px.set_mapbox_access_token(mapbox_token)

In [3]:
# get top 10 mining stocks info using a new python library called pandas_datareader
mining_stocks_df = pdr.get_data_yahoo(['AA', 'ALB', 'CLF', 'FCX', 'HL', 'NEM', 'NUE', 'SCCO', 'STLD', 'WPM', 'XME'], 
                                      start = '2015-01-01', 
                                      end = '2019-12-31'
                                     )

# extract closing prices and calculate daily returns for each stock
close_price_df = mining_stocks_df['Adj Close']
daily_returns_df = close_price_df.pct_change().dropna()

In [4]:
# set the file path
file_path = Path("Resources/Fundamental_Ratios.csv")

# create a Pandas dataframe of fundamental ratios of top 10 mining stocks
fundamental_ratios_df = pd.read_csv(file_path)

   # Data on Energy Production and Consumption

In [5]:
# set the file path
file_path = Path("Resources/Demand & Supply Gap 2010 - 2019.csv")

# create a DF for total US Energy Consumption and total US Energy Production (2010-2019)
energy_demand_supply_data = pd.read_csv(file_path)

In [6]:
#Setting paths for source files
pop2018_excel = Path("Resources/pop_by_state.xlsx")
energy_prod = Path("Resources/energy_prod_state.csv")
energy_cons_per_capita = Path("Resources/energy_cons_per_capita_state.csv")
states_long_lat = Path("Resources/states_long_lat.csv")

In [7]:
#Reading in the file of population by states
pop2018_excel = (pd.read_excel(pop2018_excel, 
                                  header = 2, #tempo note: specify the number of rows from top we want to skip by 'header' argument
                                  usecols = ["State", "Total Resident Population"],
                                  skiprows = [3,4,5,6,7,8], #tempo note: specify rows we exclude by 'skiprows' argument
                                  nrows = 51 #tempo note: specify the number of rows we want to read in by 'nrows' argument
                                 ) 
                    .set_index("State")
                   )
pop2018_excel_df = pop2018_excel.sort_index()

In [8]:
#Reading in the file of energy production by states
energy_prod2018_df = (pd.read_csv(energy_prod,
                                  usecols = ["State", "Total Energy Production, trillion Btu"]
                                 )
                      .sort_values("State")
                      .set_index("State")
                     )

In [9]:
#Reading in the file of energy consumption per capita
energy_cons2018_df = (pd.read_csv(energy_cons_per_capita,
                                  usecols = ["State", "Total Energy Consumed per Capita, million Btu"]
                                 )
                      .sort_values("State")
                      .set_index("State")
                     )

In [10]:
#Reading in the file of locations of states
states_df = (pd.read_csv(states_long_lat,
                         usecols = ["state", "latitude", "longitude"]
                        )
             .dropna()
             .set_index("state")
            )

In [11]:
#Concatonate the DFs
base_energy_data = (pd.concat
                    ([states_df, 
                      pop2018_excel_df, 
                      energy_prod2018_df, 
                      energy_cons2018_df],
                     axis = 1,
                     join = "inner"
                    )
                   )

#Convert the total energy production into per-capita numbers 
base_energy_data["Total Energy Production per Capita, million Btu"] = round(
    base_energy_data["Total Energy Production, trillion Btu"] * 1000000
        / base_energy_data["Total Resident Population"], 2)

#Drop the redundant column
base_energy_data.drop(columns = ["Total Energy Production, trillion Btu"], inplace = True)

In [12]:
#Setting a path
mines_location = Path("Resources/mines_by_location.csv")

#Reading in the file of mining locations
mines_loc_df = (pd.read_csv(mines_location,
                            usecols = ["site_name", "country", "state"]
                           )
               )

#Cleansing step 1: Exclude foreign sites
mines_loc_df = (mines_loc_df[mines_loc_df['country'] == "United States"]
                .drop(columns = "country")
               )

#Cleansing step 2: using re module, detect sites located in Puerto Rico or Virgin Islands or straddling multiple states
#Note: the code looks to regularity that the csv file has a comma b/w state names when a site straddles multiple states
#Cleansing step 3: replace the values with NaN using numpy.nan method
for idx, val in mines_loc_df.iterrows(): # tempo memo: apply for loop to each row
    val = str(mines_loc_df.loc[idx, "state"])
    match1 = re.search(", ", val) # tempo memo: re.search method examines if 1st argument is included in 2nd
    match2 = re.search("Puerto Rico", val)
    match3 = re.search("U.S. Virgin Islands", val)
    if match1 is not None:
        mines_loc_df.loc[idx, "state"] = np.nan
    elif match2 is not None:
        mines_loc_df.loc[idx, "state"] = np.nan
    elif match3 is not None:
        mines_loc_df.loc[idx, "state"] = np.nan
    else:
        pass

#Cleansing step 4: drop rows containing NaN with which we replaced the values above
mines_loc_df.dropna(axis=0, inplace=True)

#Count the number of mining sites in each state by groupby function
mining_site_count = (mines_loc_df
                     .groupby("state").count()
                     .rename(columns = {"site_name":"Number of Mining Sites"})
                    )

#Change index to abbreviation and sort index
mining_site_count.set_index(pop2018_excel.index, inplace = True)
mining_site_count.sort_index(inplace=True)

#Concatenate the DFs
energy_df = pd.concat([base_energy_data, mining_site_count], axis=1, join = "inner")
energy_df.reset_index(inplace=True)

In [13]:
# Set up API credentials
load_dotenv()

# Read the Mapbox API key
map_box_api = os.getenv("MAPBOX_API_KEY")

# Set the Mapbox API
px.set_mapbox_access_token(map_box_api)

In [14]:
# Reading in the file of historical data on production and consumption of energy by state
procon = Path("Resources/Pro_con_10years.xlsx")
procon = pd.read_excel(procon)
procon.sort_values("year", inplace= True)

   # Visualizations on Stock Financial Analysis

In [15]:
# plot rate of reurns of top 10 mining stocks vs mining index: XME
def rate_of_returns():
    rate_of_returns = daily_returns_df.hvplot(
                        kind = 'line', 
                        title = 'Rate of Returns of Mining Stocks vs Mining Index  - 2015-2019',
                        xlabel = 'Year',
                        ylabel = 'Rate of Returns (%)',
                        width = 800, 
                        height = 500 
                       )
    
    return rate_of_returns

# Boxplot to show the volatilty of the mining stocks
def mining_stocks_returns():
    mining_stocks_returns = daily_returns_df.hvplot(kind='box',
                        title="Mining Stocks Returns Compared to Mining Stocks Index - 2015-2019",
                        xlabel = 'Ticker',
                        ylabel = 'Volatility (%)',
                        width = 800, 
                        height = 500 
                       )
    
    return mining_stocks_returns

# Plot rolling standard deviations
def rolling_std_5_years():
    rolling_std_5_years = (daily_returns_df.rolling(window = 21).std()
                                           .hvplot(title = '5 Year Rolling Standard Deviation',
                                                   xlabel = 'Year',
                                                   ylabel = '5 Year Rolling Standard Deviation (%)',
                                                   ylim = (0, 0.12),
                                                   width = 800, 
                                                   height = 550
                                                  )
                          )
    
    return rolling_std_5_years

# Plot rolling standard deviations in comparison with the benchmark (XME) with a dropdown function using interact
def rolling_std_comparison(ticker):
    def roll_std_by_stock(ticker):
        ticker_line = (daily_returns_df[ticker].rolling(window = 21)
                                               .std()
                                               .hvplot(title = f'Comparison of Rolling Standard Deviation b/w ' + ticker + ' and Bechmark (XME)',
                                                       xlabel = 'Year',
                                                       ylabel = '5 Year Rolling Standard Deviation (%)',
                                                       width = 800, 
                                                       height = 500
                                                      )
                      )
            
        benchmark_line = (daily_returns_df["XME"].rolling(window = 21)
                                                 .std()
                                                 .hvplot(color = 'red')
                         )
    
        return ticker_line * benchmark_line

    # Note: In order not to show the benchmark (XME) in a dropdown, drop the 'XME' column before applying interact
    return interact(roll_std_by_stock, ticker = daily_returns_df.drop(columns = 'XME').columns)
    
# Plot a bar chart of the average rate of return
def average_rate_of_return():    
    table = daily_returns_df.describe()
    aror = (table[1:2]
        .T
        .sort_values(by = 'mean', ascending = False)
        .rename(columns = {'mean':'Rate of Return (%)'})
       )
    
    average_rate_of_return = px.bar(aror, 
                                    title = 'Average Return over Five Years - (2015-2019)',
                                    labels = {"Symbols":"Ticker", "value":"Rate of Return (%)"}
                                   )
    return average_rate_of_return

# plot stocks from cheapest to most expensive based on p/e ratio
def pe_ratio():
    pe_df = (fundamental_ratios_df[['Symbol', 'Forward P/E']]
             .sort_values('Forward P/E', ascending=False)
             .dropna()
            )
    
    pe_ratio = px.bar(pe_df, 
                      x = 'Symbol', 
                      y = 'Forward P/E', 
                      title = "Cheapest Mininig Stock by P/E",
                      labels = {"Symbol":"Ticker", "Forward P/E":"Forward P/E Ratio"}
                     )
    
    return pe_ratio

# plot the stocks from the highest dividend yielding one to the lowest one 
def dy():
    dy_df = (fundamental_ratios_df[['Symbol', 'Trailing Annual Div Yield']]
             .sort_values('Trailing Annual Div Yield', ascending=False)
             .dropna()
            )
    
    dy = px.bar(dy_df, 
                x = 'Symbol', 
                y = 'Trailing Annual Div Yield', 
                title = 'Top Mining Stock by Dividend Yield',
                labels = {'Symbol':'Ticker', 'Trailing Annual Div Yield':'Dividend Yield (%)'}
               )
    
    return dy

# plot the stocks from the one with the highest dividend rate to the lowest one
def dr():
    dr_df = (fundamental_ratios_df[['Symbol','Trailing Annual Div Rate']]
             .sort_values('Trailing Annual Div Rate', ascending=False)
             .dropna()
            )
    
    dr = px.bar(dr_df, 
                x = 'Symbol', 
                y = 'Trailing Annual Div Rate', 
                title = 'Top Mining Stock by Dividend Rate',
                labels = {'Symbol':'Ticker', 'Trailing Annual Div Rate':'Top Mining Stock by Dividend Rate ($)'}
               )
    
    return dr

# plot financial indicators using parallel coordinates
def parallel_coordinates():
    parallel_coordinates = px.parallel_coordinates(fundamental_ratios_df[['Market Cap', 
                                                                          'Forward P/E', 
                                                                          'Div/Share', 
                                                                          'Trailing Annual Div Rate', 
                                                                          'Trailing Annual Div Yield', 
                                                                          'Price/Book']], 
                                                   color = fundamental_ratios_df.index, 
                                                   color_continuous_scale=px.colors.diverging.Spectral
                                                  )
    
    return parallel_coordinates

# plot sharpe ratios
def sharpe_ratios():
    sharpe_ratios = (daily_returns_df.mean() * 252) / (daily_returns_df.std() * np.sqrt(252))
    
    sharpe_ratios = (sharpe_ratios.sort_values()
                     .hvplot(kind="bar", 
                             xlabel='Ticker', 
                             ylabel='Sharpe Ratio',
                             title='Sharpe Ratio for Mining Stocks')
                    )
    
    return sharpe_ratios

# correlation heatmap to show the correlation between the stocks and the mining index
def correlation():
    correlation_with_mining_index = daily_returns_df.corr()
    correlation = sns.heatmap(correlation_with_mining_index, cmap="YlGnBu")
    
    return correlation

In [16]:
# Create a panel
row1 = pn.Row(rate_of_returns(), 
              mining_stocks_returns()
             )

row2 = pn.Row(rolling_std_comparison(ticker = daily_returns_df.drop(columns = 'XME').columns),
              rolling_std_5_years()
             )

row3 = pn.Row(average_rate_of_return(),
              pe_ratio()
             )

row4 = pn.Row(dy(),
              dr(),
              sharpe_ratios()
             )

In [17]:
tabs1 = pn.Tabs(
    ("Volatility", row1),
    ("Standard Deviation", row2),
    ("Financial Indicators", row3),
    ("Parallel Coordinates", row4)
    )

   # Visualizations on Energy Production and Consumption

In [18]:
# plot a 3D chart
def plot_3D():
    plot_3d = px.scatter_3d(energy_demand_supply_data, 
                            x = 'Total Primary Energy Production', 
                            y = 'Year', 
                            z = 'Total Primary Energy Consumption', 
                            color = 'Year', 
                            size = 'Year'
                           )

    plot_3d.update_layout(margin = dict(l = 0, r = 0, b = 0, t = 0),
                          width = 700,
                          height = 500
                         )

    return plot_3d

# plot a plotly plot to show the gap between production and consumption
def gap_bw_prod_con():
    demand_supply_gap_plot = px.bar(energy_demand_supply_data, 
                                    x = 'Year', 
                                    y = 'Demand/Supply Gap',
                                    color = 'Year',
                                    title = 'Demand and Supply of U.S. Total Energy in quad BTUs -(2010-2019)',
                                    width = 700,
                                    height = 500
                                   )
    
    return demand_supply_gap_plot

# Create a map showing the number of mining sites in each state
def energy_map1():
    energy_map = px.scatter_mapbox(energy_df,
                                   lat = "latitude",
                                   lon = "longitude",
                                   size = "Number of Mining Sites",
                                   color = "Number of Mining Sites",
                                   title = "Number of Mining Sites in States",
                                   labels = "Number of Mining Sites",
                                   hover_name = "index",
                                   zoom = 2.5
                                  )
    
    return energy_map

# Create interactive maps of mining sites, energy production, and energy consumption with a dropdown function
def mining_sites_prod_con():
    for col in energy_df.columns:
        energy_df[col] = energy_df[col].astype(str)

    energy_df['text'] = ('Popu: ' + energy_df['Total Resident Population'] + '<br>'
                + 'Mining Sites: ' + energy_df['Number of Mining Sites'] + '<br>'
                + 'Energy Cons: ' + energy_df['Total Energy Consumed per Capita, million Btu'] + '<br>' 
                + 'Energy Prod: ' + energy_df['Total Energy Production per Capita, million Btu']
                )
    plots = []
    dropdowns = []
    cols = ["Number of Mining Sites",
          "Total Energy Consumed per Capita, million Btu", 
          "Total Energy Production per Capita, million Btu"]
    visible = np.array(cols)

    def energy_plot(columnlist):
        for col in columnlist:
            plots.append(go.Choropleth(
                locations = energy_df['index'],
                z = energy_df[col].astype(float),
                locationmode = 'USA-states',
                colorscale = 'Greens', # Reds or Greens
                autocolorscale = False,
                text = energy_df["text"],
                colorbar_title = col,
                marker_line_color = 'white',
                visible = True if col == cols[0] else False)
                )
        
            dropdowns.append(dict(label = col,
                              method = "update",
                              args = [{"visible":list(visible == col)},
                                      {"title": col}]))
    
        menus = [{"active": 0, "buttons": dropdowns, 
             "direction": "down",
             "pad": {"r": 10, "t": 10},
             "showactive": False,
             "x": -0.07,
             "xanchor": "left",
             "y": 1.2,
             "yanchor": "top"}]
    
        fig = go.Figure(data = plots, layout = dict(updatemenus = menus))

        fig.update_layout(
            title = col,
            geo_scope='usa',
            )

        return fig

    return energy_plot(cols)

# Plot the historical energy production
def historical_energy_production():
    fig = px.scatter_geo(
            procon,
            locations = 'state',
            locationmode = "USA-states",
            size = 'prod',
            size_max = 45,
            animation_frame = "year",
            color = 'prod',
            labels = {"year":"Year", "prod":"Prod", "state":"State"},
            color_continuous_scale = px.colors.cyclical.mygbm
            )

    fig.update_layout(
            title = "Energy Production 2010 - 2018 (million Btu)",
            geo_scope='usa',
            )

    return fig

# Plot the historical energy consumption
def historical_energy_consumption():
    fig = px.scatter_geo(
            procon,
            locations = 'state',
            locationmode = "USA-states",
            size = 'con',
            size_max = 45,
            animation_frame = "year",
            color = 'con',
            labels = {"year":"Year", "con":"Con", "state":"State"},
            color_continuous_scale = px.colors.cyclical.IceFire # options: Twilight, IceFire, Edge, Phase, HSV, mrybm, mygbm
            )

    fig.update_layout(
            title = "Energy Consumption 2010 - 2018 (million Btu)",
            geo_scope='usa',
            )

    return fig

In [19]:
column1 = pn.Column("# Graphs about Volatility", 
                    row1)

column2 = pn.Column("# Standard Deviation in Comparison with Benchmark",
                    row2
                   )

column3 = pn.Column("# Financial Indicators",
                    row3,
                    row4
                   )

column4 = pn.Column("# Parallel Coordinates",
                    parallel_coordinates()
                   )

In [20]:
column5 = pn.Column("# Distribution of Mining Site",
                    energy_map1()
                   )

column6 = pn.Column("# Mining Sites, Production, and Cunsumption by State",
                    mining_sites_prod_con()
                   )

column7 = pn.Column("# Energy Production by State",
                    historical_energy_production()
                   )

column8 = pn.Column("# Energy Consumption by State",
                    historical_energy_consumption()
                   )

column9 = pn.Column("# Energy Production and Consumption in the US",
                     plot_3D()
                    )

column10 = pn.Column("# Gap b/w Energy Production and Consumption in the US",
                     gap_bw_prod_con()
                    )              

In [22]:
tabs1 = pn.Tabs(
    ("Volatility", column1),
    ("Standard Deviation", column2),
    ("Financial Indicators", column3),
    ("Parallel Coordinates", column4),
    ("Mining Sites", column5),
    ("Sites/Prod/Con US", column6),
    ("Prod State", column7),
    ("Con State", column8),
    ("3D", column9),
    ("Gap", column10)
    )

In [23]:
tabs1.servable()

Tabs
    [0] Column
        [0] Markdown(str)
        [1] Row
            [0] HoloViews(NdOverlay)
            [1] HoloViews(BoxWhisker)
    [1] Column
        [0] Markdown(str)
        [1] Row
            [0] Column
                [0] Column
                    [0] Select(name='ticker', options=['AA', 'ALB', ...], value='AA')
                [1] Row
                    [0] HoloViews(Overlay, name='interactive01848')
            [1] HoloViews(NdOverlay)
    [2] Column
        [0] Markdown(str)
        [1] Row
            [0] Plotly(Figure)
            [1] Plotly(Figure)
        [2] Row
            [0] Plotly(Figure)
            [1] Plotly(Figure)
            [2] HoloViews(Bars)
    [3] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [4] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [5] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [6] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [7] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [8] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [9] Column
        [0] Markdown(str)
        [1] Plotly(Figure)